In [1]:
import numpy as np
import pandas as pd
from IPython.display import display
from tqdm import tqdm
from collections import Counter
import ast

import matplotlib.pyplot as plt
import matplotlib.mlab as mlab
import seaborn as sb

from sklearn.feature_extraction.text import CountVectorizer
from textblob import TextBlob
import scipy.stats as stats

from sklearn.decomposition import TruncatedSVD
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.manifold import TSNE

from bokeh.plotting import figure, output_file, show
from bokeh.models import Label
from bokeh.io import output_notebook
output_notebook()


from langdetect import detect

%matplotlib inline

Loading BokehJS ...

In [2]:
r=pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Capetown\\Capetown.csv")
r1= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\bejing\\reviews.csv")
r2= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Lisbon\\reviewsli.csv")
r3= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Istanbul\\reviewsI.csv")
r4= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\London\\reviewsl.csv")
r5= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\NewYork\\reviewsNW.csv")
r6= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Paris\\reviewsP.csv")
r7= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Rome\\reviewsR.csv")
r8= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Sydney\\reviewsSy.csv")
r9= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Tokyo\\reviewsT.csv")
r10= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Victoria\\reviewsV.csv")
r11= pd.read_csv("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Rio de janerio\\reviewsRi.csv")

In [3]:
r['Location']='CapeTown'
r1['Location']='Bejing'
r2['Location']='Lisbon'
r3['Location']='Istanbul'
r4['Location']='London'
r5['Location']='NewYork'
r6['Location']='Paris'
r7['Location']='Rome'
r8['Location']='Sydney'
r9['Location']='Tokyo'
r10['Location']='Victoria'
r11['Location']='Rio'

In [4]:
d=r.dropna()
d1=r1.dropna()
d2=r2.dropna()
d3=r3.dropna()
d4=r4.dropna()
d5=r5.dropna()
d6=r6.dropna()
d7=r7.dropna()
d8=r8.dropna()
d9=r9.dropna()
d10=r10.dropna()
d11=r11.dropna()

In [5]:
d=d.sample(n=50000)
d1=d1.sample(n=50000)
d2=d2.sample(n=50000)
d3=d3.sample(n=50000)
d4=d4.sample(n=50000)
d5=d5.sample(n=50000)
d6=d6.sample(n=50000)
d7=d7.sample(n=50000)
d8=d8.sample(n=50000)
d9=d9.sample(n=50000)
d10=d10.sample(n=50000)
d11=d11.sample(n=50000)

In [6]:
D=([d,d1,d2,d3,d4,d5,d6,d7,d8,d9,d10,d11])
df=pd.concat(D)

In [7]:
df

listing_id         id        date  reviewer_id     reviewer_name  \
177515    16110422  223274119  2018-01-01     56847433            Benoît   
303222    30053968  589498338  2020-01-06     25224725            Tokelo   
58755      5887352   70104109  2016-04-16     33387916  Regina & Richard   
328525    35294167  480140508  2019-07-02    141890200            Marlon   
170383    15812137  225088040  2018-01-05     54982536             Sarah   
...            ...        ...         ...          ...               ...   
197552    13841953  472851930  2019-06-20     98836656              Luîs   
264751    21792722  570038705  2019-11-28    168380070           Alegria   
254333    20242958  434786134  2019-04-08    112984849             Inger   
290779    27165477  436313821  2019-04-12     40582844            Martin   
222834    15897911  175300469  2017-07-28    126623672        Ana Flávia   

                                                 comments  Location  
177515  Sehr schöne Wohnung mit zu dem Gebäude passend...  CapeTown  
303222  The host canceled this reservation 8 days befo...  CapeTown  
58755   The cottage was a dream. Even if we had just o...  CapeTown  
328525                Very nice place! Highly recommended  CapeTown  
170383  We had a great stay! We will come again. no qu...  CapeTown  
...                                                   ...       ...  
197552  Place is great located, only two blocks away f...       Rio  
264751  Maravilhoso!!!!\n\nTudo limpo, apartamento con...       Rio  
254333  We had a great time at Mauricios place in Copa...       Rio  
290779  The host canceled this reservation 69 days bef...       Rio  
222834  Apartamento excelente, muito bem localizado, t...       Rio  

[600000 rows x 7 columns]

In [8]:
for index, row in df['comments'].iteritems():
        try:
            lang = detect(row) #detecting each row
            df.loc[index, 'Languagereveiw'] = lang
        except:
            'skip'

In [9]:
is_eng=(df['Languagereveiw']=='en')
df=df[is_eng]
print(df.shape)

(407122, 8)


In [10]:
from nltk.corpus import wordnet
def get_wordnet_pos(pos_tag):
    if pos_tag.startswith('J'):
        return wordnet.ADJ
    elif pos_tag.startswith('V'):
        return wordnet.VERB
    elif pos_tag.startswith('N'):
        return wordnet.NOUN
    elif pos_tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN
import string
from nltk import pos_tag
from nltk.corpus import stopwords
from nltk.tokenize import WhitespaceTokenizer
from nltk.stem import WordNetLemmatizer

In [11]:
import re
from nltk.corpus import stopwords
stop = stopwords.words('english')

In [12]:
def clean_text(text):
    # lower text
    text = text.lower()
    # tokenize text and remove puncutation
    text = [word.strip(string.punctuation) for word in text.split(" ")]
    # remove words that contain numbers
    text = [word for word in text if not any(c.isdigit() for c in word)]
    # remove stop words
    text = [x for x in text if x not in stop]
    # remove empty tokens
    text = [t for t in text if len(t) > 0]
    # pos tag text
    pos_tags = pos_tag(text)
    # lemmatize text
    text = [WordNetLemmatizer().lemmatize(t[0], get_wordnet_pos(t[1])) for t in pos_tags]
    # remove words with only one letter
    text = [t for t in text if len(t) > 2]
    # join all
    text = " ".join(text)
    return(text)

In [13]:
df["review_clean"] = df["comments"].apply(lambda x: clean_text(x))

C:\Users\sarka\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [14]:
import spacy
nlp = spacy.load('en_core_web_lg', parse=True, tag=True, entity=True)

In [15]:
df['noun']=""
for x in (range(len(df['review_clean']))):
    lines = str(df['review_clean'].iloc[x])
    doc =nlp(lines)
    str1=" "
    str2=" "
    for token in doc:
        if token.pos_ is 'NOUN':
            str1=str1+ " "+token.text
            df['noun'].iloc[x]=str1

C:\Users\sarka\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
C:\Users\sarka\anaconda3\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
C:\Users\sarka\anaconda3\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/us

In [16]:
from gensim.models import Word2Vec
import gensim
from gensim.models.ldamulticore import LdaMulticore
from gensim import corpora, models
import pyLDAvis.gensim
import nltk
from nltk.tokenize import word_tokenize

In [17]:
w_tokenizer = nltk.tokenize.WhitespaceTokenizer()

In [58]:
def tokenize(t):
    return [w for w in w_tokenizer.tokenize(t)]
df['text_lemmatized'] = df.review_clean.apply(tokenize)

C:\Users\sarka\anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [83]:
Model= Word2Vec(df.text_lemmatized,min_count=3,size=75,workers=2)

In [69]:
vocabulary = Model.wv.vocab

In [93]:
Host = Model.wv.most_similar('host')+ Model.wv.most_similar('communication')+Model.wv.most_similar('owner')
Ho=[]
for x in Host:
    Ho.append(x[0])
Ho.append("host")
Ho.append("communication")
Ho.remove("guest")
Ho.remove("always")
Ho

['hostess',
 'owner',
 'extremely',
 'helpful',
 'staff',
 'person',
 'job',
 'team',
 'incredibly',
 'communicate',
 'communicator',
 'communicating',
 'contact',
 'response',
 'communicative',
 'process',
 'check',
 'reply',
 'respond',
 'staff',
 'landlord',
 'host',
 'management',
 'tenant',
 'lady',
 'person',
 'guy',
 'always',
 'host',
 'communication']

In [62]:
Model.save("word2vec.model")
Model.save("model.bin")

In [45]:
Area = Model.wv.most_similar('neighbourhood')+ Model.wv.most_similar('area')
ar=[]
for x in Area:
    ar.append(x[0])
ar.append("neighbourhood")
ar.append("location")
ar

['neighborhood',
 'area',
 'district',
 'suburb',
 'surroundings',
 'street',
 'area.',
 'quarter',
 'community',
 'part',
 'neighborhood',
 'neighbourhood',
 'spot',
 'district',
 'parioli',
 'street',
 'quarter',
 'part',
 'suburb',
 'place',
 'neighbourhood',
 'location']

In [46]:
Place = Model.wv.most_similar('room')+Model.wv.most_similar('bedroom')+Model.wv.most_similar('property')
pl=[]
for x in Place:
    pl.append(x[0])
pl.append('room')
pl.append('bedroom')
pl

['bedroom',
 'space',
 'bathroom',
 'house',
 'apartment',
 'bedrooms',
 'flat',
 'toilet',
 'suite',
 'couch',
 'room',
 'bedrooms',
 'couch',
 'separate',
 'washroom',
 'upstairs',
 'sofa',
 'double',
 'mirror',
 'seat',
 'unit',
 'accommodation',
 'apartment',
 'suite',
 'apt',
 'flat',
 'house',
 'residence',
 'place',
 'condo',
 'room',
 'bedroom']

In [89]:
cl=[]
for element in Ho:
    cl.append(element.strip())
print(cl)

['hostess', 'owner', 'extremely', 'helpful', 'always', 'staff', 'person', 'job', 'team', 'incredibly', 'communicate', 'communicator', 'communicating', 'contact', 'response', 'communicative', 'process', 'check', 'reply', 'respond', 'staff', 'landlord', 'host', 'management', 'tenant', 'lady', 'person', 'guy', 'always', 'host', 'communication']


In [27]:
df['topic']=""
m=0
for x in (range(len(df['review_clean']))):
    lines = str(df['review_clean'].iloc[x])
    doc =nlp(lines)
    t=[]
    for token in doc:
        k= str(token)
        if k in pl:
            t.append("property")
        if k in ar:
            t.append("Neighbourhood")
        if k in ho:
            t.append("Host")
    df['topic'].iloc[m]=t
    print(m,t)
    m=m+1

C:\Users\sarka\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
C:\Users\sarka\anaconda3\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
C:\Users\sarka\anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/us

0 ['property', 'Host']
1 ['property', 'Neighbourhood']
2 ['Host']
3 ['property', 'Neighbourhood', 'property', 'property']
4 []
5 ['property', 'Host', 'Neighbourhood']
6 ['property', 'property', 'property']
7 ['Neighbourhood', 'property', 'property', 'property']
8 []
9 ['property']
10 ['property', 'property', 'Host', 'property']
11 []
12 ['property']
13 ['Neighbourhood']
14 ['property', 'Neighbourhood', 'property', 'property', 'Host', 'Host']
15 ['property', 'Host']
16 ['Host', 'Host']
17 ['Neighbourhood', 'property', 'property']
18 ['Neighbourhood', 'Neighbourhood', 'property', 'property', 'property', 'Host', 'property']
19 ['property', 'property', 'Host']
20 ['Host', 'property', 'property', 'Neighbourhood', 'Neighbourhood']
21 []
22 ['property', 'property', 'property', 'Host', 'property', 'property', 'Neighbourhood', 'property', 'property']
23 ['property', 'Neighbourhood', 'Host']
24 ['property', 'Neighbourhood', 'Host', 'Host']
25 ['property']
26 ['Neighbourhood', 'Neighbourhood', 'p

KeyboardInterrupt: 

In [52]:
df

listing_id         id        date  reviewer_id reviewer_name  \
223749    19939992  537941990  2019-09-29    287203614         Louis   
192230    16792655  294006841  2018-07-21     55319742          Jake   
186669    16475713  409574414  2019-02-08    200124370       Clinton   
256185    22253396  302310261  2018-08-05     43723895        Amanda   
51796      5312697   65777612  2016-03-17     51447315           Sue   
...            ...        ...         ...          ...           ...   
132226     7240684  220463118  2017-12-22      1680006       Matthew   
181538    12471832  270561448  2018-05-29    191435020      Ashantee   
330480    37364104  523391806  2019-09-03     34144485        Cowboy   
65084      2277084   14609950  2014-06-23     13101994         Glenn   
141151     8501192  149883248  2017-05-06     27882153       Jo Inge   

                                                 comments  Location  \
223749  We had a great time at Sandra’s place.\nSparkl...  CapeTown   
192230  I thoroughly enjoyed my stay at Tamar’s. The p...  CapeTown   
186669                                         Great host  CapeTown   
256185  The space is in a very charming neighborhood, ...  CapeTown   
51796   Everything was perfect for us -home from home....  CapeTown   
...                                                   ...       ...   
132226  This is a great place to stay. The street is s...       Rio   
181538  I stayed at the Exalda’s place with my 2 siste...       Rio   
330480  This place is truly amazing! It is located in ...       Rio   
65084   Loved staying at Copacabana, It was so close t...       Rio   
141151  Vania is the best host you can find in the wor...       Rio   

       Languagereveiw                                       review_clean  \
223749             en  great time sandra’s place.\nsparkling clean ac...   
192230             en  thoroughly enjoy stay tamar’s place clean cent...   
186669             en                                         great host   
256185             en  space charm neighborhood full colorful house h...   
51796              en  everything perfect home home.\r\nthank gabi robin   
...               ...                                                ...   
132226             en  great place stay street shady quiet feel quite...   
181538             en  stay exalda’s place sister really lovely time ...   
330480             en  place truly amazing locate middle copacabana g...   
65084              en  love stay copacabana close beach shop also fan...   
141151             en  vania best host find world give great service ...   

                                                     noun  \
223749                     time place photos host queries   
192230                            place location mountain   
186669                                                      
256185    space charm neighborhood facility advertisem...   
51796                                                       
...                                                   ...   
132226    place street doorman access apartment host r...   
181538    place sister time location supermarket lot p...   
330480    place view place assistant elect service par...   
65084     shop fan fest neighborhood host pick airport...   
141151                            host world service care   

                                          text_lemmatized  \
223749  [great, time, sandra’s, place., sparkling, cle...   
192230  [thoroughly, enjoy, stay, tamar’s, place, clea...   
186669                                      [great, host]   
256185  [space, charm, neighborhood, full, colorful, h...   
51796   [everything, perfect, home, home., thank, gabi...   
...                                                   ...   
132226  [great, place, stay, street, shady, quiet, fee...   
181538  [stay, exalda’s, place, sister, really, lovely...   
330480  [place, truly, amazing, locate, middle, copaca...   
65084   [love, stay, copacabana, c

In [53]:
k=0
d = pd.DataFrame(columns =['row_index','location','topics'])
l=len(df)
for a in df.topic.iteritems():
    if (a != []):
        for text in a[1]:
            d = d.append({'row_index':a[0],'location':df['Location'].iloc[k],'topics':text},ignore_index=True)
    if(k<=l):
        k=k+1

In [54]:
my_df = pd.DataFrame(columns =['row_index','location','topics'])

In [55]:
d

row_index  location         topics
0         223749  CapeTown       property
1         223749  CapeTown           Host
2         192230  CapeTown       property
3         192230  CapeTown  Neighbourhood
4         186669  CapeTown           Host
...          ...       ...            ...
366821    175876    Sydney       property
366822    175876    Sydney       property
366823    175876    Sydney  Neighbourhood
366824     72679    Sydney  Neighbourhood
366825     72679    Sydney       property

[366826 rows x 3 columns]

In [56]:
R=pd.get_dummies(d,columns=['topics'])
R

row_index  location  topics_Host  topics_Neighbourhood  topics_property
0         223749  CapeTown            0                     0                1
1         223749  CapeTown            1                     0                0
2         192230  CapeTown            0                     0                1
3         192230  CapeTown            0                     1                0
4         186669  CapeTown            1                     0                0
...          ...       ...          ...                   ...              ...
366821    175876    Sydney            0                     0                1
366822    175876    Sydney            0                     0                1
366823    175876    Sydney            0                     1                0
366824     72679    Sydney            0                     1                0
366825     72679    Sydney            0                     0                1

[366826 rows x 5 columns]

In [57]:
K=R.groupby(['location']).sum().reset_index()
K

location  topics_Host  topics_Neighbourhood  topics_property
0    Bejing       1838.0                1068.0           2949.0
1  CapeTown      10554.0                9253.0          21756.0
2  Istanbul      12624.0               11203.0          23407.0
3    Lisbon       8910.0                9364.0          20499.0
4    London      12677.0               10687.0          27403.0
5   NewYork      12814.0               11803.0          28519.0
6     Paris       9205.0               10410.0          21434.0
7      Rome      10646.0               10710.0          24212.0
8    Sydney      10521.0               10397.0          21963.0

In [ ]:
lis=df[['listing_id','Location']]

In [ ]:
K1=pd.DataFrame(lis.groupby(['Location'])['listing_id'].nunique())
K1

In [ ]:
k=K.rename(columns={'location':'Location'})
k

In [ ]:
d1= pd.merge(K1,k, on='Location')
d1

In [ ]:
d1[[ 'topics_Host','topics_Neighbourhood','topics_property']]=d1[['topics_Host','topics_Neighbourhood','topics_property']].div(d1.listing_id, axis=0)
d1

In [ ]:
c=pd.read_excel("C:\\Users\\sarka\\OneDrive\\Desktop\\Data\\Hofseted.xlsx")
C=c.rename(columns={'City':'Location'})
C

In [ ]:
final=pd.merge(C,d1,on='Location')

In [ ]:
z=pd.DataFrame(final)
corrMatrix = z.corr()
print(corrMatrix)

In [ ]:
f, ax = plt.subplots(figsize=(20, 15))

heatmap = sb.heatmap(corrMatrix,
                      square = True,
                      linewidths = .5,
                      cmap = 'coolwarm',
                      cbar_kws = {'shrink': .4,
                                'ticks' : [-1, -.5, 0, 0.5, 1]},
                      vmin = -1,
                      vmax = 1,
                      annot = True,
                      annot_kws = {"size": 0})

#add the column names as labels
ax.set_yticklabels(corrMatrix.columns, rotation = 0)
ax.set_xticklabels(corrMatrix.columns)

sb.set_style({'xtick.bottom': True}, {'ytick.left': True})

In [ ]:
d4=final[['Location','topics_area','topics_host','topics_place']]
d4=pd.melt(d4,id_vars=['Location'])
d4

In [ ]:
d4['variable'].iloc[21]

In [ ]:
ax = sb.boxplot(x="variable", y="value", data=d4)

###### pip3 install pandas